# ARIM-Academy：　機器データ利活用ユースケース
### 機器：誘導結合プラズマ発光分光分析法（ICP-OES）
### 分析：TPE最適化


## データセット

    
本編で扱う 『茶の元素分析データセット』（data.xlsx）、は、ブラックセイロン(BC)、ブラックトルコ(BT)、グリーンセイロン(GC)、グリーントルコ(GT)の4種類の茶葉について、3つの濃度（1%、2%、3%）で抽出したサンプルの誘導結合プラズマ発光分光分析法（ICP-OES）の元素分析データです。[1]

この研究では、機械学習（回帰分析としてMLR, ANN、および主成分分析、ISOMAP、階層クラスタ分析など）の手法を使い、茶の品種、濃度、浸出時間によるミネラル組成の変化を調査し、特定のミネラルレベルを調整する条件を見つける検討が行われています。

[1] Durmus, Y., Atasoy, A.D. & Atasoy, A.F. Mathematical optimization of multilinear and artificial neural network regressions for mineral composition of different tea types infusions. Sci Rep 14, 18285 (2024). https://doi.org/10.1038/s41598-024-69149-1

---
<br>  
<img src="./img/main_image.jpg" width="50%">
<br> 

---

**Chemical composition** 
* 9種類の元素分析値（Al, Ca, Cu, Fe,K,Mg,Mn,Na,Zn） 

**Experimental parameters**  
* Concentration：　お茶の濃度
* time:　抽出時間

**Label**
* grouped:　品種・色・濃度・抽出時間を識別できる一種の飼料名（MLは使用せず） 
* teaConc:　濃度ラベル（MLは使用せず）
* tea_org:　色ラベル（MLは使用せず）
* tea_var:　品種ラベル（MLは使用せず）
* tea：　　 色と品種ラベル（MLで使用）

### 教材への接続
google colabにおけるオンラインの場合にこのラインを実行します。（<font color="red">Google colabに接続しない場合には不要</font>）

In [ ]:
!git clone https://github.com/ARIM-Usecase/Example_2.git
%cd Example_2

### ライブラリのインポート
コード実行で必要なpythonのライブラリをimport文でロードします。

In [10]:
#汎用ライブラリ
import numpy as np
import pandas as pd
from plotly.io import show

# 回帰分析
from sklearn.linear_model import LinearRegression
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Input

# TPE最適化（Optuna）
import optuna
from optuna.samplers import TPESampler

## 1.データセットの読み込みと前処理


### サンプルファイルの読み込み
pandasライブラリのread_excel()関数は、Excelファイルを読み込んでpandasのDataFrame形式に変換する関数です。ここでは[data]フォルダーにあるdata.xlsxファイルをDataFrameとして読み込み、その結果をdfという変数に格納します。168のサンプルに対して16の特徴量からなるデータ行列となっています。

In [2]:
# データの読み込み
df= pd.read_excel('./data/data.xlsx', header = 1)
df

In [ ]:
# 特徴量とターゲットの分離
X = df[['Concentration', 'time']]
y_Fe = df['Fe']
y_Al = df['Al']
y_Mn = df['Mn']

### Optuna目的関数の定義

In [4]:
# 目的関数の定義 (MLR 用)
def objective_mlr(trial):
    # MLR モデルの定義
    model = LinearRegression()

    # 試行による最適化パラメータ
    X_train = pd.DataFrame({
        'Concentration': [trial.suggest_float('Concentration', 1.0, 3.0)],
        'time': [trial.suggest_float('time', 2.0, 60.0)]
    })
    
    # モデルのトレーニング
    model.fit(X, y_Fe)

    # 予測
    y_pred_Fe = model.predict(X_train)
    y_pred_Al = model.predict(X_train)
    y_pred_Mn = model.predict(X_train)

    # 目的関数の計算（Fe の最大化、Al の最小化、Mn の安定化）
    return -((y_pred_Fe[0] - y_pred_Al[0]) - abs(y_pred_Mn[0] - 5.3))

### Optuna最適化実行

In [5]:
# Optunaによる最適化 (MLR)
study_mlr = optuna.create_study(direction='minimize', 
                                sampler=TPESampler()
                                )

study_mlr.optimize(objective_mlr, n_trials=500)

# 最適解の表示
print(f"MLR 最適解: {study_mlr.best_params}")

[I 2024-09-15 20:46:38,843] A new study created in memory with name: no-name-ce93a4aa-6d12-48f0-833c-5e2f69dc9f6c
[I 2024-09-15 20:46:38,858] Trial 0 finished with value: 5.11955860418249 and parameters: {'Concentration': 2.884445437844952, 'time': 30.112970198640195}. Best is trial 0 with value: 5.11955860418249.
[I 2024-09-15 20:46:38,865] Trial 1 finished with value: 5.143671353000948 and parameters: {'Concentration': 1.2911146569821967, 'time': 51.831492541769}. Best is trial 0 with value: 5.11955860418249.
[I 2024-09-15 20:46:38,870] Trial 2 finished with value: 5.136299952530651 and parameters: {'Concentration': 1.8237896169837682, 'time': 44.11822658985038}. Best is trial 0 with value: 5.11955860418249.
[I 2024-09-15 20:46:38,876] Trial 3 finished with value: 5.205759347447921 and parameters: {'Concentration': 1.0721910181245469, 'time': 16.2694346305177}. Best is trial 0 with value: 5.11955860418249.
[I 2024-09-15 20:46:38,886] Trial 4 finished with value: 5.149147580499317 and

MLR 最適解: {'Concentration': 2.9995872351689545, 'time': 59.985922609111086}


### 可視化プロット

In [6]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_optimization_history(study_mlr)

fig.update_layout(width=800, height=600, 
                  showlegend=False
                  )  # 凡例を非表示に設定

show(fig)

In [7]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_contour(study_mlr)

fig.update_layout(width=800, height=600, 
                  showlegend=False
                  )  # 凡例を非表示に設定
show(fig)


In [8]:
# 目的関数の定義 (ANN 用)
def objective_ann(trial):
    # ANN モデルの定義
    model = Sequential()
    model.add(Input(shape=(2,)))  # input_dim の代わりに Input レイヤーを使用
    model.add(Dense(16, activation='relu'))
    model.add(Dense(16, activation='relu'))
    model.add(Dense(1, activation='linear'))

    # 最適化アルゴリズムと損失関数
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # 試行による最適化パラメータ
    X_train = np.array([[trial.suggest_float('Concentration', 1.0, 3.0),
                         trial.suggest_float('time', 2.0, 60.0)]])
    
    # モデルのトレーニング
    model.fit(X, y_Fe, epochs=10, verbose=0)

    # 予測
    y_pred_Fe = model.predict(X_train)
    y_pred_Al = model.predict(X_train)
    y_pred_Mn = model.predict(X_train)

    # 目的関数の計算（Fe の最大化、Al の最小化、Mn の安定化）
    return -((y_pred_Fe[0][0] - y_pred_Al[0][0]) - abs(y_pred_Mn[0][0] - 5.3))


In [11]:
# Optunaによる最適化 (ANN)
study_ann = optuna.create_study(direction='minimize', 
                                sampler=TPESampler()
                                )

study_ann.optimize(objective_ann, n_trials=100)
print(f"ANN 最適解: {study_ann.best_params}")

[I 2024-09-15 20:52:33,498] A new study created in memory with name: no-name-dde5ba02-fe08-4d09-94a8-c1456d3ea6a7


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step


[I 2024-09-15 20:52:35,002] Trial 0 finished with value: 5.032443124055862 and parameters: {'Concentration': 1.8055096133008022, 'time': 18.567238995424727}. Best is trial 0 with value: 5.032443124055862.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step


[I 2024-09-15 20:52:36,254] Trial 1 finished with value: 5.1962864503264425 and parameters: {'Concentration': 1.04788505838621, 'time': 42.863197748169014}. Best is trial 0 with value: 5.032443124055862.


...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 84ms/step


[I 2024-09-15 20:56:06,032] Trial 98 finished with value: 4.581332552433014 and parameters: {'Concentration': 2.408900337246379, 'time': 8.092331678729245}. Best is trial 36 with value: 3.1819832801818846.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step


[I 2024-09-15 20:56:07,455] Trial 99 finished with value: 5.087350937724113 and parameters: {'Concentration': 2.3907721289888744, 'time': 8.047121389198711}. Best is trial 36 with value: 3.1819832801818846.


ANN 最適解: {'Concentration': 2.3453642573185456, 'time': 27.97621420255195}


### 可視化プロット

In [12]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_optimization_history(study_ann)

fig.update_layout(width=800, height=600, 
                  showlegend=False
                  )  # 凡例を非表示に設定
show(fig)


In [13]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_contour(study_ann)
fig.update_layout(width=800, height=600, 
                  showlegend=False
                  )  # 凡例を非表示に設定
show(fig)


In [14]:
# 結果のプロット (スライスプロット)
fig = optuna.visualization.plot_slice(study_ann)
fig.update_layout(width=800, height=600, 
                  showlegend=False
                  )  # 凡例を非表示に設定
show(fig)
